<table>
<tr>
<td width="100%">
  
# **Transport calculation using EPWpy**

Author: **Sabyasachi Tiwari (11/06/2025)**


In this notebook, we compute the phonon-limited carrier

mobility of silicon using the ab initio Boltzmann Transport Equation (BTE). Electrons and phonons

are computed with Quantum ESPRESSO (QE), maximally-localized Wannier functions

are computed with Wannier90, and transport properties are computed with EPW.

Steps in **bold** are mandatory while steps not in bold can be skipped. However, we

reccommend going through all steps for an overall learning experience
</td>
<td width="500%">

**MATCSSI**

<img src="https://matcssi.tacc.utexas.edu/media/filer_public_thumbnails/filer_public/9f/1e/9f1ebcd2-8f80-4142-bcdf-b9c262c6b62d/matccsi-home-banner.jpg__1400x1400_q85_subsampling-2.jpg" width="1000">

For running dense calculations

please visit [MATCSSI](https://matcssi.tacc.utexas.edu/)


</td>
</tr>
</table>

## **Step 1: Get linux packages to build QE**
Skip this step if you already have all these libraries installed.

Note: In a single session you need this once!

In [ ]:
!apt-get -y update
!apt-get -y install m4 make wget curl git gfortran gcc libopenblas-dev libfftw3-dev libopenmpi-dev tar libxrender1

## **Step 2: We next get EPWpy**
We clone it from GitLab and then install QE+EPW inside EPWpy



In [ ]:
%cd /content
#!pip uninstall EPWpy-basic # Use this if you have multiple EPWpy versions installed
!git clone https://gitlab.com/epwpy/epwpy.git


## **Step 3: Checkout to current branch and install QE**

In [ ]:
%cd /content/epwpy
!git checkout sabyadk/EPWpy_v1.1_n
!python setup.py install --withQE True --configs 'with-scalapack=no DFLAGS="-D__FFTW3 -D__MPI" FFT_LIBS="-lfftw3"' --cores 8


## Step 3.5: Lets check if we have all the executables for QE+EPW installed by EPWpy
We also check the version of EPWpy which should be 1.1


In [ ]:
!ls /content/epwpy/build/q-e-EPW-5.9s/bin/
!pip show EPWpy-basic


## **Step 4: Starting transport calculation**
We start by building the EPWpy object with structure directly downloaded from materials project. EPWpy will automatically download pseudopotential. If it gives an error please use


In [ ]:
!pip install mp-api

### **Restart** kernel before starting calculations so that the installations take effect

In [ ]:
%cd /content
!pwd
!pip show EPWpy-basic
!ls /usr/local/lib/python3.12/dist-packages/EPWpy_basic-1.1.dev1-py3.12.egg

import EPWpy
from EPWpy import EPWpy as EP

silicon = EP.EPWpy({'structure_mp':"mp-149"},
                   system = 'si')
#silicon = EP.EPWpy({'structure':"POSCAR_mp-149"},
 #                  system = 'si')

## Step 5: A few sanity checks
We check the lattice structure, atomic positions and atomic species. We also check the location of QE executables if they are correctly obtained by EPWpy

In [ ]:
print(silicon.structure_params_summary)
print('code location:',silicon.code)

## Step 6: We plot the structure of silicon and lattice
Here we check the unit-cell and the atomic positions

In [ ]:

app = silicon.display_lattice(supercell=[2,4,2],
                              view={'wrap':False,
                                    'show_bond_length':False,'show':True,'atom_size_factor':100})


## **Step 7: We provide the environment variables and run a SCF calculation**
Here we perform the self-consistent field calculation to obtain the electron charge density of silicon in the ground state. The calculation consists of three separate steps:
1. Apply the method `scf` to the object `silicon`. This step specifies runtime parameters for an SCF calculation on siicon
2. Based on the properties defined at step 1 as well as other properties that are set by default within EPWpy, the method `prepare` creates the input file needed by QE
3. The method `run` applied to the object `silicon` instructs QE to perform the SCF calculation

In [ ]:
silicon.env = ''  # We don't have mpi in google colab
silicon.run_serial = True
silicon.scf(control={'calculation':'\'scf\''},
            kpoints={'kpoints':[[3,3,3]],
                     'kpoints_type': 'automatic'})
silicon.prepare(1,'scf')
silicon.run(1,type_run='scf',parallelization='-nk 1')
silicon.pw_util = silicon.PW_utilities() # We get the utilities here


## Step 7.5: Lets grab some utilities from EPWpy

In [ ]:
print(f'Fermi level: {silicon.pw_util.efermi} eV')
print(f'Total energy: {silicon.pw_util.total_energy} Ry')

## Step 8: We get the band structure of silicon for sanity check

In [ ]:
silicon.scf(control={'calculation':'\'bands\''},
            system={'nbnd':12},
            kpoints={'kpoints':[
                                ['0.5','0.50','0.50','10'],
                                ['0.0','0.00','0.00','10'],
                                ['0.5','0.25','0.75','10']
                               ],
                     'kpoints_type':'{crystal_b}'
                    },
            name='bs')
silicon.verbosity = 2
silicon.prepare(type_run='bs')
silicon.run(1,type_run='bs')

## Step 8.5: We plot the band structure using EPWpy
We now plot the electronic band structure computed at the previous step. The zero of the energy axis is set to the value specified manually via `ef0`.

In [ ]:
from EPWpy.plotting import plot_bands

ef_from_file = silicon.pw_util.efermi

Band=plot_bands.plot_band_scf(f'./{silicon.system}/bs/bs.out') # This is the location of band structure
plot_bands.plot_band_prod(Band,
                          ef0=ef_from_file,
                          xticks=['X',r'$\Gamma$','L'],
                          xlabel = 'Wavevector',
                          ylabel = 'Energy (eV)'
                         )

## **Step 9: We now perform a phonon (DFPT) calculation**
To compute phonon-limited mobilities, we need to determine vibrational frequencies and eigenmodes. This operation consists of three steps
1. We compute these properties on a uniform and centered Brillouin zone grid
2. We perform a Fourier transform of the results in order to obtain the interatomic force constants (IFCs)
3. We interpolate the IFCs along specified Brillouin zone paths to obtain phonon dispersions.

This plot of phonon dispersions is only meant for us to develop a qualitative understanding of the vibrational properties of the system under consideration. The phonon interpolation needed for transport calculations is performed once again later by EPW.

In [ ]:
silicon.ph(phonons={'nq1':3,
                    'nq2':3,
                    'nq3':3})
silicon.prepare(1,'ph')
silicon.run(1,type_run='ph',parallelization='-nk 1')

## Step 9.5: We grab Phonon utilities

In [ ]:
silicon.ph_util = silicon.PH_utilities()

In [ ]:
print(f'Dielectric matrix: \n {silicon.ph_util.ph_properties()}')

## Step 10: We perform the inter-atomic force constant calculation

In [ ]:
silicon.q2r(name='q2r')
silicon.prepare(type_run='q2r')
silicon.run(1,type_run='q2r')

## Step 11: We perform a matdyn calculation to get phonon spectra

In [ ]:
silicon.matdyn(name='matdyn',
               kpoints={'kpoints':[
                                   ['0.5','0.50','0.50','20'],
                                   ['0.0','0.00','0.00','20'],
                                   ['0.5','0.25','0.75','20']
                                 ],
                        'kpoints_type':'{crystal_b}'
                       },

              )

print(silicon.matdyn_input)
silicon.prepare(type_run='matdyn')
silicon.run(4,type_run='matdyn')

## Step 11.5: We plot the phonon dispersion of Si

In [ ]:
Band=plot_bands.plot_band_eig(f'./{silicon.prefix}/ph/si.freq')
plot_bands.plot_band_freq(Band[:,:],
                          ylabel='E ($cm^{-1}$)',
                          ef0=0,
                          xticks=['L',r'$\Gamma$','X'],
                          color='royalblue')

## **Step 12: We now get the wavefunctions using NSCF calculations**
Compute Kohn-Sham states on a uniform centered Brillouin zone grid (QE)


In [ ]:
silicon.nscf(system={'nbnd':12},
             kpoints={'grid':[3,3,3],'kpoints_type': 'crystal'})
silicon.prepare(1,'nscf')
silicon.run(1,type_run='nscf',parallelization='-nk 1')

## **Step 13: We perform a coarse EPW calculation**

Now we have Kohn-Sham wavefunctions and variations of the self-consistent Kohn-Sham potential on coarse Brillouin zone grid. We will generate the electron Hamiltonian, the IFCs, and the electron-phonon matrix elements in the Wannier representation using [EPW](https://epw-code.org/). Details on the underlying formalism can be found [here](https://arxiv.org/abs/1603.06965) (free version) or [here](https://doi.org/10.1103/RevModPhys.89.015003) (journal version).

This operation involves three logicals steps:
1. Use EPW to load these states and call Wannier90 to generate Wannier functions
2. Use EPW to load IFCs and potential variations, and combine with 2. to compute electron-phonon matrix elements in the Bloch representation
3. Use EPW to perform the transformation to the Wannier basis and write to file

In [ ]:

silicon.filkf_file = '\'LGX.txt\''
silicon.epw(epwin={'wdata':['guiding_centres = .true.',
                            'dis_num_iter = 500',
                            'num_print_cycles  = 10',
                            'dis_mix_ratio = 1',
                            'use_ws_distance = T'],
                   'proj':['\'Si : sp3\''],
                   'band_plot':'.true.',
                   'filkf':silicon.filkf_file,
                   'filqf':silicon.filkf_file,
                   'etf_mem':0,
                   'fsthick':12.0,
                   'wannierize':'.true.',
                   'wannier_plot':'.true.',
                   'wannier_plot_radius':'5.0',
                   'elph':'.true.',
                   'num_iter':500,
                   'calc_nelec_wann': '.false.',
                  },
            name='epw1')
silicon.filkf_file = 'LGX.txt'
silicon.filkf(path=[[0.5,0.5,0.5],
                    [0.0,0.0,0.0],
                    [0.5,0.25,0.75]],
              length=[51,51],
             )
silicon.prepare(type_run='epw1')
silicon.run(1,type_run='epw1')

## Step 13.5: We plot the silicon Wannier functions

In [ ]:
from EPWpy.utilities import *
from EPWpy.plotting.plot_wannier_matplotlib import *
epw_util = silicon.EPW_utilities()
epw_util.plot_wannier()

## Step 14: We next plot the bandstructure and phonon dispersions obtained from EPW and QE
At this point we have all necessary quantities in the Wannier representation on file. As a sanity check, we perform a simple interpolation of bands and phonons to make sure that we reproduce the results found above _without_ Wannier interpolation.
The match won't be exact since the grids are too coarse.

In [ ]:
Band_EPW=plot_bands.plot_band_eig(f'./{silicon.prefix}/epw/band.eig') # Location of EPW output
Band_QE=plot_bands.plot_band_scf(f'./{silicon.prefix}/bs/bs.out') # Location of DFT output

plot_bands.plot_band_prod(Band_EPW,
                          ef0=ef_from_file,
                          xlabel='Wavevector',
                          ylabel='Electron energy (eV)',
                          xticks=['L','G','X'],linestyle='--',color_c='b',color_v='b',first = True)
plot_bands.plot_band_prod(Band_QE,
                          ef0=ef_from_file,
                          xlabel='Wavevector',
                          ylabel='Electron energy (eV)',
                          xticks=['L','G','X'],first = False) # False controls if this is the first set of plots
# Phonons

PH_epw=plot_bands.plot_band_eig(f'./{silicon.prefix}/epw/phband.freq')
PH_matdyn=plot_bands.plot_band_eig(f'./{silicon.prefix}/ph/si.freq')
PH_matdyn=PH_matdyn*0.124


plot_bands.plot_band_freq(PH_epw,
                          xlabel='Wavevector',
                          ylabel='Phonon energy (meV)',
                          ef0=0,
                          xticks=['L','G','X'],linestyle='--',first = True,color='blue')

plot_bands.plot_band_freq(PH_matdyn,
                          xlabel='Wavevector',
                          ylabel='Phonon energy (meV)',
                          ef0=0,
                          xticks=['L','G','X'],first = False)

## **Step 15: We next calculate the hole mobility of Si**

In order to compute the carrier mobility, we perform the following operations:
1. We interpolate the electrons, phonons, and electron-phonon couplings onto a fine Brillouin zone grid (60 x 60 x 60 for electrons and phonons in this example)
2. We use these data to solve the BTE within EPW

Both steps are performed within a single call of EPW. Note the keyword `temps` which is used to perform calculations for multiple temperatures (300 K, ..., 100 K in this example).

In [ ]:
#silicon.reset()
silicon.epw(epwin={'elph':'.true.',
                   'nkf1':30,
                   'nkf2':30,
                   'nkf3':30,
                   'nqf1':30,
                   'nqf2':30,
                   'nqf3':30,
                   'mp_mesh_k':'.true.',
                   'efermi_read':'.true.',
                   'fsthick': 0.4,
                   'etf_mem':1,
                   'fermi_energy':6.5,
                   'temps':'300 250 200 150 100',
                   'degaussw':0.0,
                   'nstemp': 5,
                   'transport_calc':'hole' # This allows for hole-mobility calculation
                   },
            name='epw2')
silicon.prepare(type_run='epw2')
silicon.run(1,type_run='epw2')


## **Step 16: We plot the mobility which we obtain using property class of EPW**
Since the google colab allows only one core, the grids are extremely coarse. Hence, the mobilities are not converged.

In [ ]:
silicon.epw_file = 'epw2'
temps=[300, 250, 200, 150, 100]
mob=[]
font=16
for T in temps:
    silicon.epw_params['temps']=T
    print(silicon.ibte_mobility_h[0,0],T)
    mob.append(silicon.ibte_mobility_h[1,1])
    plt.scatter(T,silicon.ibte_mobility_h[1,1], color = 'crimson')
    plt.scatter(T,silicon.serta_mobility_h[1,1], color = 'royalblue')
print(mob)
plt.plot(temps[::-1],mob[::-1], color = 'crimson')
plt.xticks([100,150,200,250,300],fontsize=font)
plt.yticks([500,1000,2000,3000],fontsize=font)
plt.xlabel('Temperature (K)',fontsize=16)
plt.ylabel(r'$\mu$ (cm$^2$V$^{-1}$s$^{-1}$)',fontsize=16)
plt.xticks(fontsize=16)
plt.yticks(fontsize=16)
plt.show()